In [1]:
# Install necessary libraries
!pip install joblib
!pip install mealpy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.9/104.9 kB 873.8 kB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.3/386.3 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 60.7 MB/s eta 0:00:00


In [2]:
import numpy as np
import json
import time
from mealpy.swarm_based import HBA
from mealpy.utils.space import FloatVar
from mealpy import GA


In [3]:
#  task and VM counts to test
task_counts = [100, 375, 750, 1000]
vm_counts = [30, 45, 60, 75, 90]

# pr values to test
pr_values = [0.0, 0.1, 0.25, 0.5, 0.75, 0.9, 1.0]

In [4]:
# Iterate over each combination of task count, VM count, and pr value
for taskcount in task_counts:
    for vmcount in vm_counts:
        # Initialize the VM capacities
        VM = [1000] * vmcount  # Homogeneous VM capacities

        for pr in pr_values:
            print(f"Running experiment with {taskcount} tasks, {vmcount} VMs, and pr={pr}")

            # Define the objective function
            def Fun(solution):
                list1 = [0] * vmcount
                for i in range(solution.size):
                    solution[i] = round(solution[i])
                    index = min(max(int(solution[i]) - 1, 0), len(list1) - 1)
                    list1[index] += taskcount / VM[index]
                return min(list1)

            # Define the Problem Dictionary for the Algorithm
            problem_dict = {
                "bounds": FloatVar(lb=[0 for i in range(taskcount)], ub=[vmcount - 1 for i in range(taskcount)], name="delta"),
                "minmax": "min",
                "obj_func": Fun,
                "verbose": True,
                "name": f"Problem Objective for HGA with Task Count: {taskcount} and VM Count: {vmcount}",
                "log_to": "console",
            }

            # HBA Configuration
            hba_params = {
                'epoch': 100,
                'pop_size': 100,
                'pr': pr,
                'name':"HBA for initial set of solution",
            }

            # GA Configuration
            ga_params = {
                'epoch': 50,
                'pop_size': 100,
                'pc': 0.9,
                'pm': 0.1,
                'selection': 'tournament',
                'crossover': 'uniform',
                'mutation': 'flip',
                'name':"Refine solutions using GA",
            }

            # Run HBA to get an initial set of solutions
            start_time = time.time()
            hba_model = HBA.OriginalHBA(**hba_params)
            hba_solution = hba_model.solve(problem_dict)
            hba_solutions = [hba_solution.solution]

            # Refine solutions using GA
            ga_model = GA.BaseGA(**ga_params)
            refined_solutions = []

            for initial_solution in hba_solutions:
                problem_dict["bounds"].ub = [vmcount - 1] * taskcount
                problem_dict["bounds"].lb = [0] * taskcount
                refined_solution = ga_model.solve(problem_dict)
                refined_solutions.append(refined_solution)

            exetime = time.time() - start_time

            # Get the best solution from GA
            best_solution = min(refined_solutions, key=lambda sol: sol.target.fitness)

            best_solution_list = [int(round(num)) for num in best_solution.solution]

            print(f"Best Solution from Embedded Approach for {taskcount} tasks, {vmcount} VMs, and pr={pr}: {best_solution_list}")
            print(f"Total execution time of Embedded Approach for {taskcount} tasks, {vmcount} VMs, and pr={pr}: {exetime} seconds")

            # Save results to JSON
            output_data = {
                "name": [str(num) for num in best_solution_list],
                "exetime": exetime
            }

            filename = f"Hybrid_HBA_GA_results_tasks_{taskcount}_vms_{vmcount}_pr_{pr}.json"
            with open(filename, "w") as outfile:
                json.dump(output_data, outfile, ensure_ascii=False, indent=4)

            print(f"Results saved to {filename}\n")

INFO:mealpy.swarm_based.HBA.OriginalHBA:Solving single objective optimization problem.
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 1, Current best: 0.0, Global best: 0.0, Runtime: 0.03346 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 2, Current best: 0.0, Global best: 0.0, Runtime: 0.03228 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 3, Current best: 0.0, Global best: 0.0, Runtime: 0.03240 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 4, Current best: 0.0, Global best: 0.0, Runtime: 0.03304 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 5, Current best: 0.0, Global best

Running experiment with 100 tasks, 30 VMs, and pr=0.0


INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 6, Current best: 0.0, Global best: 0.0, Runtime: 0.03460 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 7, Current best: 0.0, Global best: 0.0, Runtime: 0.03534 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 8, Current best: 0.0, Global best: 0.0, Runtime: 0.03580 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 9, Current best: 0.0, Global best: 0.0, Runtime: 0.03196 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 10, Current best: 0.0, Global best: 0.0, Runtime: 0.03217 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Pr

Best Solution from Embedded Approach for 100 tasks, 30 VMs, and pr=0.0: [5, 14, 0, 2, 23, 3, 28, 12, 28, 15, 7, 25, 9, 21, 4, 20, 3, 23, 18, 16, 13, 2, 10, 1, 16, 13, 11, 22, 12, 7, 23, 27, 2, 27, 23, 13, 25, 9, 3, 5, 20, 2, 18, 11, 27, 8, 0, 29, 23, 15, 16, 21, 3, 4, 7, 8, 8, 24, 22, 11, 28, 18, 27, 22, 13, 20, 16, 5, 13, 1, 24, 19, 20, 22, 18, 17, 19, 12, 16, 18, 24, 2, 18, 2, 6, 13, 15, 28, 12, 8, 7, 28, 18, 24, 20, 18, 0, 16, 1, 9]
Total execution time of Embedded Approach for 100 tasks, 30 VMs, and pr=0.0: 5.809526205062866 seconds
Results saved to Hybrid_HBA_GA_results_tasks_100_vms_30_pr_0.0.json

Running experiment with 100 tasks, 30 VMs, and pr=0.1


INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 5, Current best: 0.0, Global best: 0.0, Runtime: 0.03490 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 6, Current best: 0.0, Global best: 0.0, Runtime: 0.03386 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 7, Current best: 0.0, Global best: 0.0, Runtime: 0.03268 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 8, Current best: 0.0, Global best: 0.0, Runtime: 0.03556 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 100 and VM Count: 30, Epoch: 9, Current best: 0.0, Global best: 0.0, Runtime: 0.03405 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Pro

...

Best Solution from Embedded Approach for 1000 tasks, 90 VMs, and pr=0.75: [72, 44, 33, 26, 67, 69, 54, 12, 60, 79, 49, 47, 60, 70, 36, 10, 75, 23, 47, 26, 29, 21, 58, 29, 52, 10, 15, 75, 7, 20, 80, 16, 57, 62, 81, 47, 67, 59, 70, 2, 61, 67, 59, 22, 63, 28, 87, 84, 81, 47, 1, 72, 80, 45, 52, 56, 57, 30, 63, 48, 52, 34, 14, 53, 14, 14, 76, 74, 24, 10, 27, 46, 13, 72, 20, 10, 87, 68, 81, 39, 29, 39, 73, 52, 10, 23, 54, 83, 57, 47, 82, 89, 66, 32, 22, 31, 68, 28, 0, 74, 79, 37, 22, 85, 19, 6, 45, 62, 33, 53, 35, 14, 54, 13, 7, 57, 3, 67, 15, 27, 75, 82, 11, 69, 65, 51, 10, 47, 29, 79, 73, 48, 50, 59, 6, 63, 12, 25, 76, 9, 25, 54, 35, 76, 68, 62, 18, 88, 24, 31, 79, 48, 13, 54, 56, 33, 9, 17, 3, 46, 74, 39, 47, 49, 21, 71, 62, 56, 1, 16, 44, 19, 83, 25, 60, 46, 59, 55, 44, 53, 42, 7, 47, 52, 4, 57, 47, 67, 88, 65, 56, 14, 74, 83, 73, 87, 57, 42, 59, 68, 2, 18, 5, 35, 21, 31, 39, 78, 64, 37, 13, 83, 77, 6, 50, 87, 22, 37, 5, 78, 60, 10, 24, 88, 51, 40, 77, 18, 66, 85, 87, 45, 56, 56, 62, 20,

INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 1, Current best: 0.0, Global best: 0.0, Runtime: 0.23208 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 2, Current best: 0.0, Global best: 0.0, Runtime: 0.22396 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 3, Current best: 0.0, Global best: 0.0, Runtime: 0.22387 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 4, Current best: 0.0, Global best: 0.0, Runtime: 0.22012 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 5, Current best: 0.0, Global best: 0.0, Runtime: 0.22659 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem

Best Solution from Embedded Approach for 1000 tasks, 90 VMs, and pr=0.9: [59, 21, 58, 9, 87, 73, 50, 46, 48, 0, 49, 45, 16, 44, 75, 15, 82, 61, 88, 35, 69, 8, 2, 54, 38, 18, 70, 52, 18, 48, 58, 26, 7, 6, 16, 84, 83, 34, 24, 89, 46, 42, 31, 11, 36, 20, 4, 62, 59, 11, 42, 8, 77, 46, 65, 84, 24, 76, 41, 64, 11, 60, 8, 21, 1, 33, 15, 29, 61, 31, 39, 56, 74, 14, 59, 83, 41, 69, 82, 12, 41, 52, 38, 25, 25, 16, 17, 81, 21, 15, 80, 55, 39, 24, 19, 68, 27, 66, 13, 38, 63, 80, 73, 76, 3, 66, 76, 43, 19, 76, 52, 15, 76, 42, 69, 8, 9, 60, 80, 24, 88, 10, 66, 11, 16, 70, 80, 11, 78, 63, 30, 27, 4, 41, 62, 13, 54, 40, 80, 62, 73, 46, 36, 15, 73, 72, 37, 13, 17, 76, 89, 11, 87, 57, 55, 85, 18, 84, 73, 39, 26, 25, 63, 81, 16, 12, 86, 50, 57, 52, 85, 81, 68, 67, 88, 76, 50, 12, 5, 8, 88, 6, 46, 72, 3, 79, 76, 50, 45, 58, 38, 51, 36, 26, 77, 83, 24, 76, 81, 38, 78, 8, 31, 9, 64, 10, 28, 3, 16, 0, 83, 59, 56, 36, 61, 50, 40, 39, 71, 70, 63, 29, 2, 34, 11, 50, 0, 79, 29, 78, 62, 47, 34, 42, 13, 62, 41, 51

INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 1, Current best: 0.0, Global best: 0.0, Runtime: 0.22177 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 2, Current best: 0.0, Global best: 0.0, Runtime: 0.21798 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 3, Current best: 0.0, Global best: 0.0, Runtime: 0.21644 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 4, Current best: 0.0, Global best: 0.0, Runtime: 0.21634 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem: Problem Objective for HGA with Task Count: 1000 and VM Count: 90, Epoch: 5, Current best: 0.0, Global best: 0.0, Runtime: 0.22326 seconds
INFO:mealpy.swarm_based.HBA.OriginalHBA:>>>Problem

Best Solution from Embedded Approach for 1000 tasks, 90 VMs, and pr=1.0: [11, 19, 6, 40, 1, 73, 3, 50, 15, 55, 48, 44, 67, 29, 51, 84, 57, 46, 63, 78, 47, 11, 69, 72, 78, 69, 61, 58, 14, 39, 22, 23, 10, 31, 1, 88, 8, 8, 74, 13, 51, 8, 42, 16, 72, 82, 54, 3, 62, 13, 75, 44, 27, 50, 17, 16, 59, 32, 43, 61, 22, 54, 13, 22, 87, 78, 65, 2, 20, 1, 86, 77, 38, 41, 29, 61, 82, 55, 70, 77, 56, 53, 27, 74, 65, 12, 1, 24, 75, 38, 65, 4, 28, 58, 32, 46, 65, 85, 7, 32, 8, 57, 59, 6, 33, 7, 85, 14, 34, 42, 48, 28, 44, 36, 64, 58, 63, 79, 34, 71, 37, 58, 1, 76, 34, 30, 74, 48, 46, 14, 33, 35, 59, 68, 15, 87, 38, 19, 70, 88, 44, 8, 71, 46, 25, 2, 8, 48, 71, 1, 30, 66, 13, 53, 82, 4, 34, 68, 85, 49, 64, 45, 78, 88, 9, 56, 40, 10, 8, 61, 45, 60, 85, 28, 56, 67, 59, 79, 23, 20, 59, 75, 80, 66, 43, 45, 79, 51, 34, 20, 75, 75, 21, 74, 53, 44, 71, 5, 62, 37, 73, 8, 57, 75, 78, 34, 14, 73, 0, 23, 54, 67, 78, 14, 53, 78, 59, 21, 62, 65, 87, 7, 28, 51, 61, 67, 23, 12, 30, 52, 49, 60, 32, 80, 10, 37, 19, 62, 2,